In [8]:
import h5py, numpy
from pycbc.conversions import mchirp_from_mass1_mass2

f = h5py.File('../combined.hdf', 'r')
m1b = f['mass1'][:]
m2b = f['mass2'][:]
mcb = mchirp_from_mass1_mass2(m1b, m2b)
print len(m1b)

4030479


In [9]:
import os
os.environ['HMR_FILE'] = '../s.hdf'
from pycbc.waveform import get_td_waveform, get_fd_waveform
import pycbc.psd
from pycbc.filter import match

bf = 128
sr = 4096
tlen = bf * sr
flen = int(tlen / 2 + 1)
fl = 20
df = 1.0 / bf
dt = 1.0 / sr

p = pycbc.psd.from_txt('../H1L1-AVERAGE_PSD-1163174417-604800.txt', flen, df, fl)

### EOB mathes HMR model ###

In [3]:
m1 = 21
m2 = 0.1
hp, hc = get_td_waveform(approximant="EOBNRv2", mass1=m1, mass2=m2, f_lower=fl,
                         delta_t=dt, coa_phase=0.3)

if len(hp) > tlen:
    hp = hp[len(hp)-tlen:]
hp.resize(tlen)

if len(hc) > tlen:
    hc = hc[len(hc)-tlen:]
hc.resize(tlen) 

hp2, hc2 = get_fd_waveform(approximant="HMR", mass1=m1, mass2=m2, f_lower=fl, delta_f=df)
hp2.resize(flen)
import pylab

hp2 = hp2.to_timeseries()

pylab.plot(hp.sample_times, hp)
pylab.plot(hp2.sample_times, hp2)
match(hp, hp2, psd=p, low_frequency_cutoff=20)

(0.9901696095177219, 204)

### Bank is reasonably self-consistent ###

In [59]:
from pycbc.conversions import tau0_from_mass1_mass2

m1 = 20
m2 = .012

tau0 = tau0_from_mass1_mass2(m1, m2, 15.0)
tau0b = tau0_from_mass1_mass2(m1b, m2b, 15.0)

k = abs(tau0 - tau0b) < 1.0
m1t = m1b[k]
m2t = m2b[k]
print len(m1t)


#hp, hc = get_td_waveform(approximant="EOBNRv2", mass1=m1, mass2=m2, f_lower=fl,
#                         delta_t=dt, coa_phase=0.3)

#if len(hp) > tlen:
#    hp = hp[len(hp)-tlen2:]
#hp.resize(tlen)

#if len(hc) > tlen:
#    hc = hc[len(hc)-tlen2:]
#hc.resize(tlen)    
hp, hc = get_fd_waveform(approximant="HMR", mass1=m1, mass2=m2, delta_f=df, f_lower=fl, duration=30.0)
hp.resize(flen)

ff = 0
for m1g, m2g in zip(m1t, m2t):
    hp2, hc2 = get_fd_waveform(approximant="HMR", mass1=m1g, mass2=m2g, f_lower=fl, delta_f=df, duration=30.0)
    hp2.resize(flen)

    m = match(hp, hp2, psd=p**0.5, low_frequency_cutoff=25)[0]
    if m > ff:
        ff = m
        print ff, m1g, m2g
    if ff > 0.97:
        break

684
0.08253417225947095 0.010500862528156466 24.435731201494217
0.44666191354191004 0.011960072405172769 20.104449891420213
0.5187396614139498 0.011972698451323012 20.071213945176893
0.8500365112528014 0.011995199352720002 20.015618293538672


In [27]:
m1 = 20
m2 = .011

from pycbc.conversions import tau0_from_mass1_mass2
tau0 = tau0_from_mass1_mass2(m1, m2, 15.0)
tau0b = tau0_from_mass1_mass2(m1b, m2b, 15.0)

print tau0, tau0b

k = abs(tau0 - tau0b) < 1.0
m1t = m1b[k]
m2t = m2b[k]
print len(m1t)


5834.5144175 [  22.57665414   22.96901105   22.5275006  ... 6307.96435121 6307.96616623
 6306.65526576]
253


### Higher modes ####

In [10]:
for m1 in [20.0, 50.0, 100.0]:
    for m2 in [1, .1, .05, .01]:
        inc = [0, 1.0, 1.4, 1.7]
        for i in inc:
            hp, hc = get_td_waveform(approximant="EOBNRv2HM", mass1=m1, mass2=m2, f_lower=fl, delta_t=dt, inclination=i, coa_phase=0.3)

            print len(hp)
            if len(hp) > tlen:
                hp = hp[len(hp)-tlen:]
            hp.resize(tlen)

            if len(hc) > tlen:
                hc = hc[len(hc)-tlen:]
            hc.resize(tlen)    

            hp2, hc2 = get_fd_waveform(approximant="HMR", mass1=m1, mass2=m2, f_lower=fl, delta_f=df)
            fmin = hp2.sample_frequencies[hp2.abs_arg_max()]
            
            fcut = int(fmin) + 5
            print "FLOW", fmin, fcut
            
            hp2.resize(flen)

            o1 = match(hp, hp2, psd=p, low_frequency_cutoff=fcut)[0]
            o2 = match(hc, hp2, psd=p, low_frequency_cutoff=fcut)[0]
            o3 = match(hp, hc, psd=p, low_frequency_cutoff=fcut)[0]

            print m1, m2, i, o1, o2, o3

119744
FLOW 20.4296875 25
20.0 1 0 0.9991264404252795 0.999152005142786 0.9999166890989953
119744
FLOW 20.4296875 25
20.0 1 1.0 0.9340687320215969 0.9359592657883794 0.9994996392171895
119744
FLOW 20.4296875 25
20.0 1 1.4 0.9080840337863777 0.9126815908995268 0.9982966747515748
119744
FLOW 20.4296875 25
20.0 1 1.7 0.9068177719264865 0.9115975732561555 0.9981977501870561
1174277
FLOW 29.4765625 34
20.0 0.1 0 0.9987320775303696 0.9987494356487343 0.9999876522518928
1174277
FLOW 29.4765625 34
20.0 0.1 1.0 0.9225234131728363 0.9236761752955134 0.9997349907014267
1174277
FLOW 29.4765625 34
20.0 0.1 1.4 0.8935492556285712 0.8963706164701255 0.9990175757188762
1174277
FLOW 29.4765625 34
20.0 0.1 1.7 0.892166136612676 0.8951029435539156 0.9989588215059408
2345890
FLOW 37.484375 42
20.0 0.05 0 0.9899689003287008 0.989968527505436 0.9999919744335686
2345890
FLOW 37.484375 42
20.0 0.05 1.0 0.88829755988092 0.901189135284844 0.9965686658565419
2345890
FLOW 37.484375 42
20.0 0.05 1.4 0.836431196572

/home/ahnitz/projects/env/lib/python2.7/site-packages/PyCBC-1rc4903-py2.7-linux-x86_64.egg/pycbc/types/array.py:381: RuntimeWarning: divide by zero encountered in true_divide
  self._data /= other
/home/ahnitz/projects/env/lib/python2.7/site-packages/PyCBC-1rc4903-py2.7-linux-x86_64.egg/pycbc/scheme.py:190: RuntimeWarning: divide by zero encountered in divide
  return _import_cache[mgr.state][fn](*args, **kwds)
/home/ahnitz/projects/env/lib/python2.7/site-packages/PyCBC-1rc4903-py2.7-linux-x86_64.egg/pycbc/scheme.py:190: RuntimeWarning: invalid value encountered in divide
  return _import_cache[mgr.state][fn](*args, **kwds)


FLOW 10.0625 15
50.0 1 1.0 nan nan nan
54253
FLOW 10.0625 15
50.0 1 1.4 nan nan nan
54253
FLOW 10.0625 15
50.0 1 1.7 nan nan nan
532862
FLOW 22.0078125 27
50.0 0.1 0 0.9995238381492583 0.9994301141448015 0.9999249365084932
532862
FLOW 22.0078125 27
50.0 0.1 1.0 0.44270722222210435 0.5503894925577902 0.978456518501797
532862
FLOW 22.0078125 27
50.0 0.1 1.4 0.35436766864361174 0.4906263883945858 0.9596906643488927
532862
FLOW 22.0078125 27
50.0 0.1 1.7 0.3507005852563127 0.48854010634064393 0.9586348797388451
1064566
FLOW 27.3046875 32
50.0 0.05 0 0.9980047164320802 0.9980631386831346 0.9999508372965411
1064566
FLOW 27.3046875 32
50.0 0.05 1.0 0.47879329942478865 0.5988690992704452 0.973528471685647
1064566
FLOW 27.3046875 32
50.0 0.05 1.4 0.37100515968686887 0.5376734360734648 0.94952743159213
1064566
FLOW 27.3046875 32
50.0 0.05 1.7 0.36645788636879884 0.5351956788567345 0.9481818212958165
5317962
FLOW 42.3046875 47
50.0 0.01 0 0.9928481116080856 0.9928496620153384 0.9999792409297691
5